<a href="https://colab.research.google.com/github/Srajan1122/Hyperspectral_Image_Classification/blob/srajan/MLP.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
from scipy import io
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
from sklearn.preprocessing import OneHotEncoder 
from sklearn import preprocessing

In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


## Loading DataSet
### Dataset include image and a ground truth

In [0]:
loaded_dataset = io.loadmat('/content/drive/My Drive/Srajan/Internship/SEM4-LeadingindiaAI/Tasks/Datasets/IndianPines/Indian_pines_corrected.mat')
image = loaded_dataset['indian_pines_corrected']

In [0]:
ground_truth = io.loadmat('/content/drive/My Drive/Srajan/Internship/SEM4-LeadingindiaAI/Tasks/Datasets/IndianPines/Indian_pines_gt.mat')
ground_truth = ground_truth['indian_pines_gt']

### Class Labels

In [0]:
label_values = ["Alfalfa", "Corn-notill", "Corn-mintill",
                        "Corn", "Grass-pasture", "Grass-trees",
                        "Grass-pasture-mowed", "Hay-windrowed", "Oats",
                        "Soybean-notill", "Soybean-mintill", "Soybean-clean",
                        "Wheat", "Woods", "Buildings-Grass-Trees-Drives",
                        "Stone-Steel-Towers"]

### Resizing the data

In [0]:
image_with_gt = np.dstack((image, ground_truth))

In [0]:
final_output = image_with_gt.reshape(ground_truth.size, image.shape[2]+1)

### Visualizing data in pandas

In [0]:
data = pd.DataFrame(final_output)

In [0]:
data.head()

0     1     2     3     4     5    ...   195   196   197   198   199  200
0  3172  4142  4506  4279  4782  5048  ...  1062  1069  1057  1020  1020    3
1  2580  4266  4502  4426  4853  5249  ...  1079  1085  1064  1029  1020    3
2  3687  4266  4421  4498  5019  5293  ...  1065  1092  1061  1030  1016    3
3  2749  4258  4603  4493  4958  5234  ...  1071  1088  1060  1030  1006    3
4  2746  4018  4675  4417  4886  5117  ...  1072  1087  1052  1034  1019    3

[5 rows x 201 columns]

### Droping the row if ground_truth value is zero

In [0]:
print("Percentage of column which will be droped",(data.size - data[data[200] == 0].size)/data.size,"%")

Percentage of column which will be droped 0.48746730083234247 %


In [0]:
data = data[data.iloc[:, -1] != 0]

### Spliting the data into feature and target

In [0]:
X = data.iloc[:, :-1]
y = data.iloc[:,-1]

### Correlation between the features

In [0]:
import seaborn as sns
import matplotlib.pyplot as plt

plt.figure(figsize=(150, 200))
sns.heatmap(X.corr(), annot=True, vmin=-1, vmax=1, center= 0)

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


### Feature Selection


In [0]:
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2, f_classif, mutual_info_classif

X = SelectKBest(f_classif, k=150).fit_transform(X, y)

### OneHotEncoding the target column

In [0]:
onehotencoder = OneHotEncoder() 
y = onehotencoder.fit_transform(np.array(y).reshape(-1,1)).toarray() 

### Standardizing the feature columns

In [0]:
X = preprocessing.scale(X)

### Spliting the data into training and testing set 

In [0]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.15, random_state=1)#0.25 0.15

In [0]:
np.unique(y_train.argmax(axis=1), return_counts=True)

(array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15]),
 array([  40, 1208,  705,  195,  411,  625,   24,  407,   18,  829, 2096,
         488,  177, 1073,  327,   88]))

## Preparing ANN model 
### Defining the model

Link to learn about the parameters
https://scikit-learn.org/stable/modules/generated/sklearn.neural_network.MLPClassifier.html

In [0]:
model = MLPClassifier(hidden_layer_sizes=(150, 150, 150, 150, 150),
                      activation='relu',
                      solver='adam',
                      alpha=0.0001,
                      batch_size='auto',
                      learning_rate='constant',
                      learning_rate_init=0.001,
                      power_t=0.5,
                      max_iter=600,
                      shuffle=True,
                      random_state=1,
                      tol=0.0001,
                      verbose=False,
                      warm_start=False,
                      momentum=0.9,
                      nesterovs_momentum=True,
                      early_stopping=False,
                      validation_fraction=0.18,#0.33 0.18
                      beta_1=0.9,
                      beta_2=0.999,
                      epsilon=1e-08,
                      n_iter_no_change=50,
                      max_fun=15000)

### Fitting the model

In [0]:
model.fit(X_train,y_train)

MLPClassifier(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(150, 150, 150, 150, 150),
              learning_rate='constant', learning_rate_init=0.001, max_fun=15000,
              max_iter=600, momentum=0.9, n_iter_no_change=50,
              nesterovs_momentum=True, power_t=0.5, random_state=1,
              shuffle=True, solver='adam', tol=0.0001, validation_fraction=0.18,
              verbose=False, warm_start=False)

## Accuracy

In [0]:
model.score(X_train,y_train)

0.9994260130869016

# Prediction 

In [0]:
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score, classification_report, confusion_matrix,cohen_kappa_score
prediction = model.predict(X_test)

In [0]:
accuracy_score(y_test, prediction)

0.9271781534460338

In [0]:
precision_score(y_test, prediction,average="weighted")

0.9385339590794454

In [0]:
recall_score(y_test, prediction, average="weighted")

0.9330299089726918

In [0]:
f1_score(y_test, prediction, average="weighted")

0.9354746785374273

In [0]:
cohen_kappa_score(y_test.argmax(axis=1), prediction.argmax(axis=1), labels=list(x for x in range(1,17)), weights=None, sample_weight=None)

0.9329327261677642

In [0]:
print(classification_report(y_test, prediction, target_names=label_values))

                              precision    recall  f1-score   support

                     Alfalfa       0.86      1.00      0.92         6
                 Corn-notill       0.97      0.90      0.93       220
                Corn-mintill       0.94      0.93      0.93       125
                        Corn       0.90      0.88      0.89        42
               Grass-pasture       0.97      0.94      0.96        72
                 Grass-trees       0.96      0.98      0.97       105
         Grass-pasture-mowed       1.00      1.00      1.00         4
               Hay-windrowed       1.00      0.97      0.99        71
                        Oats       1.00      1.00      1.00         2
              Soybean-notill       0.94      0.96      0.95       143
             Soybean-mintill       0.92      0.94      0.93       359
               Soybean-clean       0.98      0.97      0.98       105
                       Wheat       1.00      1.00      1.00        28
                   

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
